In [30]:
import matplotlib.pyplot as plt
import os
import torch
import numpy as np
import random 

import torch.optim as optim
import argparse
import torch.nn as nn

from torch.utils.data import DataLoader
from torchvision import datasets
from torchvision.transforms import ToTensor

from tqdm import tqdm
from torch import Tensor
from typing import Type


In [31]:
def get_data(batch_size=64):
    # CIFAR10 training dataset.
    dataset_train = datasets.CIFAR10(
        root='data',
        train=True,
        download=True,
        transform=ToTensor(),
    )
    # CIFAR10 validation dataset.
    dataset_valid = datasets.CIFAR10(
        root='data',
        train=False,
        download=True,
        transform=ToTensor(),
    )
    # Create data loaders.
    train_loader = DataLoader(
        dataset_train, 
        batch_size=batch_size,
        shuffle=True
    )
    valid_loader = DataLoader(
        dataset_valid, 
        batch_size=batch_size,
        shuffle=False
    )
    return train_loader, valid_loader

In [33]:
# Training function.
def train(model, trainloader, optimizer, criterion, device):
    model.train()
    print('Training')
    train_running_loss = 0.0
    train_running_correct = 0
    counter = 0
    for i, data in tqdm(enumerate(trainloader), total=len(trainloader)):
        counter += 1
        image, labels = data
        image = image.to(device)
        labels = labels.to(device)
        optimizer.zero_grad()
        # Forward pass.
        outputs = model(image)
        # Calculate the loss.
        loss = criterion(outputs, labels)
        train_running_loss += loss.item()
        # Calculate the accuracy.
        _, preds = torch.max(outputs.data, 1)
        train_running_correct += (preds == labels).sum().item()
        # Backpropagation
        loss.backward()
        # Update the weights.
        optimizer.step()
    
    # Loss and accuracy for the complete epoch.
    epoch_loss = train_running_loss / counter
    # epoch_acc = 100. * (train_running_correct / len(trainloader.dataset))
    epoch_acc = 100. * (train_running_correct / len(trainloader.dataset))
    return epoch_loss, epoch_acc

In [34]:
# Validation function.
def validate(model, testloader, criterion, device):
    model.eval()
    print('Validation')
    valid_running_loss = 0.0
    valid_running_correct = 0
    counter = 0
    with torch.no_grad():
        for i, data in tqdm(enumerate(testloader), total=len(testloader)):
            counter += 1
            
            image, labels = data
            image = image.to(device)
            labels = labels.to(device)
            # Forward pass.
            outputs = model(image)
            # Calculate the loss.
            loss = criterion(outputs, labels)
            valid_running_loss += loss.item()
            # Calculate the accuracy.
            _, preds = torch.max(outputs.data, 1)
            valid_running_correct += (preds == labels).sum().item()
        
    # Loss and accuracy for the complete epoch.
    epoch_loss = valid_running_loss / counter
    epoch_acc = 100. * (valid_running_correct / len(testloader.dataset))
    return epoch_loss, epoch_acc

In [35]:
class BasicBlock(nn.Module):
    def __init__(
        self, 
        in_channels: int,
        out_channels: int,
        stride: int = 1,
        expansion: int = 1,
        downsample: nn.Module = None
    ) -> None:
        super(BasicBlock, self).__init__()
        # Multiplicative factor for the subsequent conv2d layer's output channels.
        # It is 1 for ResNet18 and ResNet34.
        self.expansion = expansion
        self.downsample = downsample
        self.conv1 = nn.Conv2d(
            in_channels, 
            out_channels, 
            kernel_size=3, 
            stride=stride, 
            padding=1,
            bias=False
        )
        self.bn1 = nn.BatchNorm2d(out_channels)
        self.relu = nn.ReLU(inplace=True)
        self.conv2 = nn.Conv2d(
            out_channels, 
            out_channels*self.expansion, 
            kernel_size=3, 
            padding=1,
            bias=False
        )
        self.bn2 = nn.BatchNorm2d(out_channels*self.expansion)
    def forward(self, x: Tensor) -> Tensor:
        identity = x
        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)
        out = self.conv2(out)
        out = self.bn2(out)
        if self.downsample is not None:
            identity = self.downsample(x)
        out += identity
        out = self.relu(out)
        return  out

In [36]:
class ResNet(nn.Module):
    def __init__(self, img_channels: int, num_layers: int,
        block: Type[BasicBlock],
        num_classes: int  = 1000) -> None:
        super(ResNet, self).__init__()
        if num_layers == 18:
           
            layers = [2, 2, 2, 2]
            self.expansion = 1
        
        self.in_channels = 64
       
        self.conv1 = nn.Conv2d(in_channels=img_channels, out_channels=self.in_channels,
            kernel_size=7, stride=2, padding=3,
            bias=False)
        self.bn1 = nn.BatchNorm2d(self.in_channels)
        self.relu = nn.ReLU(inplace=True)
        self.maxpool = nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        self.layer1 = self._make_layer(block, 64, layers[0])
        self.layer2 = self._make_layer(block, 128, layers[1], stride=2)
        self.layer3 = self._make_layer(block, 256, layers[2], stride=2)
        self.layer4 = self._make_layer(block, 512, layers[3], stride=2)
        self.avgpool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(512*self.expansion, num_classes)
    def _make_layer(self, block: Type[BasicBlock], out_channels: int, blocks: int,
        stride: int = 1) -> nn.Sequential:
        downsample = None
        if stride != 1:
            downsample = nn.Sequential(nn.Conv2d(self.in_channels, out_channels*self.expansion, kernel_size=1,
                    stride=stride, bias=False ),nn.BatchNorm2d(out_channels * self.expansion),)
        layers = []
        layers.append(block(self.in_channels, out_channels, stride, self.expansion, downsample))
        
        self.in_channels = out_channels * self.expansion
        for i in range(1, blocks):
            layers.append(block(self.in_channels,out_channels,expansion=self.expansion))
        return nn.Sequential(*layers)
   
    def forward(self, x: Tensor) -> Tensor:
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        x = self.maxpool(x)
        x = self.layer1(x)
        x = self.layer2(x)
        x = self.layer3(x)
        x = self.layer4(x)

        print('Dimensions of the last convolutional feature map: ', x.shape)
        x = self.avgpool(x)
        x = torch.flatten(x, 1)
        x = self.fc(x)
        return x

In [37]:
if __name__ == '__main__':
    tensor = torch.rand([1, 3, 224, 224])
    model = ResNet(img_channels=3, num_layers=18, block=BasicBlock, num_classes=1000)
    print(model)
    
    # Total parameters and trainable parameters.
    total_params = sum(p.numel() for p in model.parameters())
    print(f"{total_params:,} total parameters.")
    total_trainable_params = sum(
        p.numel() for p in model.parameters() if p.requires_grad)
    print(f"{total_trainable_params:,} training parameters.")
    output = model(tensor)

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
  

In [38]:
seed = 42
torch.manual_seed(seed)
torch.cuda.manual_seed(seed)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = True
np.random.seed(seed)
random.seed(seed)

In [39]:
# Learning and training parameters.
epochs = 20
batch_size = 64
learning_rate = 0.01
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
train_loader, valid_loader = get_data(batch_size=batch_size)

model = ResNet(img_channels=3, num_layers=18, block=BasicBlock, num_classes=10).to(device)

# Total parameters and trainable parameters.
total_params = sum(p.numel() for p in model.parameters())
print(f"{total_params:,} total parameters.")
total_trainable_params = sum(
    p.numel() for p in model.parameters() if p.requires_grad)
print(f"{total_trainable_params:,} training parameters.")
# Optimizer.
optimizer = optim.SGD(model.parameters(), lr=learning_rate)
# Loss function.
criterion = nn.CrossEntropyLoss()

Files already downloaded and verified
Files already downloaded and verified
11,181,642 total parameters.
11,181,642 training parameters.


In [42]:
if __name__ == '__main__':
    # Lists to keep track of losses and accuracies.
    train_loss, valid_loss = [], []
    train_acc, valid_acc = [], []
    # Start the training.
    for epoch in range(epochs):
        print(f"[INFO]: Epoch {epoch+1} of {epochs}")
        train_epoch_loss, train_epoch_acc = train(
            model, 
            train_loader, 
            optimizer, 
            criterion,
            device
        )
        valid_epoch_loss, valid_epoch_acc = validate(
            model, 
            valid_loader, 
            criterion,
            device
        )
        train_loss.append(train_epoch_loss)
        valid_loss.append(valid_epoch_loss)
        train_acc.append(train_epoch_acc)
        valid_acc.append(valid_epoch_acc)
        print(f"Training loss: {train_epoch_loss:.3f}, training acc: {train_epoch_acc:.3f}")
        print(f"Validation loss: {valid_epoch_loss:.3f}, validation acc: {valid_epoch_acc:.3f}")
        print('-'*50)

    print('TRAINING COMPLETE')

[INFO]: Epoch 1 of 20
Training


  0%|                                           | 1/782 [00:00<06:13,  2.09it/s]

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])


  0%|▏                                          | 3/782 [00:01<06:31,  1.99it/s]

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])


...

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])


 99%|████████████████████████████████████████▍| 155/157 [00:51<00:00,  3.03it/s]

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])


100%|█████████████████████████████████████████| 157/157 [00:51<00:00,  3.03it/s]

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([16, 512, 1, 1])
Training loss: 0.046, training acc: 98.460
Validation loss: 1.387, validation acc: 72.520
--------------------------------------------------
TRAINING COMPLETE


In [55]:
# Check several images.
dataiter = iter(valid_loader)
images, labels = next(dataiter)
imshow(torchvision.utils.make_grid(images))
print('GroundTruth: ', ' '.join('%5s' % classes[labels[j]] for j in range(4)))
outputs = model(images.to(device))
_, predicted = torch.max(outputs, 1)

print('Predicted: ', ' '.join('%5s' % classes[predicted[j]]
                              for j in range(4)))

NameError: name 'imshow' is not defined

In [43]:
correct = 0
total = 0

with torch.no_grad():
    for data in valid_loader:
        images, labels = data
        images, labels = images.to(device), labels.to(device)
        outputs = model(images)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

print('Accuracy of the network on the validation dataset: %d %%' % (
    100 * correct / total))

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  t

In [54]:
class_correct = list(0. for i in range(10))
class_total = list(0. for i in range(10))
with torch.no_grad():
    for data in valid_loader:
        images, labels = data
        images, labels = images.to(device), labels.to(device)
        outputs = model(images)
        _, predicted = torch.max(outputs, 1)
        c = (predicted == labels).squeeze()
        for i in range(4):
            label = labels[i]
            class_correct[label] += c[i].item()
            class_total[label] += 1

for i in range(10):
    print('Accuracy of %5s : %2d %%' % (
        classes[i], 100 * class_correct[i] / class_total[i]))

Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  torch.Size([64, 512, 1, 1])
Dimensions of the last convolutional feature map:  t